In [1]:
%matplotlib inline
# import sys
# reload(sys)
# sys.setdefaultencoding('utf-8')
import re
import csv
import pandas as pd
import string
from string import digits
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.porter import PorterStemmer
from collections import Counter
import matplotlib as mpl
import matplotlib.pyplot as plt
from subprocess import check_output
#from wordcloud import WordCloud
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.cross_validation import train_test_split
from pandas import *
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn import metrics
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn import linear_model
import numpy as np

/Users/ventinalimbong/anaconda3/lib/python3.5/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
data = pd.read_csv('./Downloads/IMDB Dataset.csv')

In [3]:
import pandas as pd

In [4]:
len(data)

50000

In [5]:
list(data.columns.values)

['review', 'sentiment']

In [6]:
data.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [7]:
pos = len([x for x in data['sentiment'] if x == 'positive'])
neg = len([x for x in data['sentiment'] if x == 'negative'])
neg, pos,''

(25000, 25000, '')

#split the dataset  
#train dataset
train_reviews = data.review[:30000]
train_sentiment = data.sentiment[:30000]
#test dataset
test_reviews = data.review[30000:]
test_sentiment = data.sentiment[30000:]

#Shape of train & test dataset
print('Shape of train dataset::',train_reviews.shape,train_sentiment.shape)
print('Shape of test dataset::',test_reviews.shape,test_sentiment.shape)

# Pre-Processing Training Set and Validation¶
### 1. Case Folding
Convert text into lower case

In [8]:
pd.set_option('display.max_colwidth', -1)
for i in range(len(data)):
    lowercase = str.lower(data['review'].iloc[i])
    data['review'].iloc[i]=lowercase
print ('Data train case folding...')
data.head()

Data train case folding...


review  \
0  one of the other reviewers has mentioned that after watching just 1 oz episode you'll be hooked. they are right, as this is exactly what happened with me.<br /><br />the first thing that struck me about oz was its brutality and unflinching scenes of violence, which set in right from the word go. trust me, this is not a show for the faint hearted or timid. this show pulls no punches with regards to drugs, sex or violence. its is hardcore, in the classic use of the word.<br /><br />it is called oz as that is the nickname given to the oswald maximum security state penitentary. it focuses mainly on emerald city, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. em city is home to many..aryans, muslims, gangstas, latinos, christians, italians, irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.<br /><br />i would say the main appeal of the show is due to the fact that it goes where other shows wouldn't dare. forget pretty pictures painted for mainstream audiences, forget charm, forget romance...oz doesn't mess around. the first episode i ever saw struck me as so nasty it was surreal, i couldn't say i was ready for it, but as i watched more, i developed a taste for oz, and got accustomed to the high levels of graphic violence. not just violence, but injustice (crooked guards who'll be sold out for a nickel, inmates who'll kill on order and get away with it, well mannered, middle class inmates being turned into prison bitches due to their lack of street skills or prison experience) watching oz, you may become comfortable with what is uncomfortable viewing....thats if you can get in touch with your darker side.   
1  a wonderful little production. <br /><br />the filming technique is very unassuming- very old-time-bbc fashion and gives a comforting, and sometimes discomforting, sense of realism to the entire piece. <br /><br />the actors are extremely well chosen- michael sheen not only "has got all the polari" but he has all the voices down pat too! you can truly see the seamless editing guided by the references to williams' diary entries, not only is it well worth the watching but it is a terrificly written and performed piece. a masterful production about one of the great master's of comedy and his life. <br /><br />the realism really comes home with the little things: the fantasy of the guard which, rather than use the traditional 'dream' techniques remains solid then disappears. it plays on our knowledge and our senses, particularly with the scenes concerning orton and halliwell and the sets (particularly of their flat with halliwell's murals decorating every surface) are terribly well done.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
2  i thought this was a wonderful way to spend time on a too hot summer weekend, sitting in the air conditioned theater and watching a light-hearted comedy. the plot is simplistic, but the dialogue is witty and the characters are likable (even the well bread suspected serial killer). while some may be disappointed when they realize this is not match point 2: risk addiction, i thought it was proof that woody allen is still fully in control of the styl

### 2. Normalization
Convert words into normalized words, convert negation, and remove punctuations.

In [10]:
# Convert words into normalized words
normalization = csv.reader(open('./Downloads/Corpus/normalisasi.csv', 'r'))

d = {}
for row in normalization:
    k,v= row
    d[str.lower(k)] = str.lower(v)
pat = re.compile(r"\b(%s)\b" % "|".join(d))

for i in range(len(data)):
    text = str.lower(data['review'].iloc[i])
    normal = pat.sub(lambda m: d.get(m.group()), text)
    data['review'].iloc[i]=normal 
print ('Data train normalization...')
data.head(20)

Data train normalization...


review  \
0   one of the other reviewers has mentioned that after watching just 1 oz episode you will be hooked. they are right, as this is exactly what happened with me.<br /><br />the first thing that struck me about oz was it is brutality and unflinching scenes of violence, which set in right from the word go. trust me, this is not a show for the faint hearted or timid. this show pulls no punches with regards to drugs, sex or violence. it is is hardcore, in the classic use of the word.<br /><br />it is called oz as that is the nickname given to the oswald maximum security state penitentary. it focuses mainly on emerald city, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. em city is home to many..aryans, muslims, gangstas, latinos, christians, italians, irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.<br /><br />i would say the main appeal of the show is due to the fact that it goes where other shows would not dare. forget pretty pictures painted for mainstream audiences, forget charm, forget romance...oz does not mess around. the first episode i ever saw struck me as so nasty it was surreal, i could not say i was ready for it, but as i watched more, i developed a taste for oz, and got accustomed to the high levels of graphic violence. not just violence, but injustice (crooked guards who'll be sold out for a nickel, inmates who'll kill on order and get away with it, well mannered, middle class inmates being turned into prison bitches due to their lack of street skills or prison experience) watching oz, you may become comfortable with what is uncomfortable viewing....that is if you can get in touch with your darker side.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
1   a wonderful little production. <br /><br />the filming technique is very unassuming- very old-time-bbc fashion and gives a comforting, and sometimes discomforting, sense of realism to the entire piece. <br /><br />the actors are extremely well chosen- michael sheen not only "has got all the polari" but he has all the voices down pat too! you can truly see the seamless editing guided by the references to williams' diary entries, not only is it well worth the watching but it is a terrificly written and performed piece. a masterful production about one of the great master's of comedy and his life. <br /><br />the realism really comes home with the little things: the fantasy of the guard which, rather than use the traditional 'dream' techniques remains solid then disappears. it plays on our knowledge and our senses, particularly with the scenes concerning orton and halliwell and the sets (particularly of their flat with halliwell's murals decorating every surface) are terribly well done.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [11]:
# Convert Negation
negation = csv.reader(open('./Downloads/Corpus/convert negation.csv', 'r'))

d = {}
for row in negation:
    k,v= row
    d[str.lower(k)] = str.lower(v)
    #print d[k]
pat = re.compile(r"\b(%s)\b" % "|".join(d))
for i in range(len(data)):
    convert = str.lower(data['review'].iloc[i])
    convert = pat.sub(lambda m: d.get(m.group()), convert)
    data['review'].iloc[i]=convert
print ('Data train negation word converting...')
data.head(20)

Data train negation word converting...


review  \
0   one of the other reviewers has mentioned that after watching just 1 oz episode you will be hooked. they are right, as this is exactly what happened with me.<br /><br />the first thing that struck me about oz was it is brutality and unflinching scenes of violence, which set in right from the word go. trust me, this is not a show for the faint hearted or timid. this show pulls no punches with regards to drugs, sex or violence. it is is hardcore, in the classic use of the word.<br /><br />it is called oz as that is the nickname given to the oswald maximum security state penitentary. it focuses mainly on emerald city, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. em city is home to many..aryans, muslims, gangstas, latinos, christians, italians, irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.<br /><br />i would say the main appeal of the show is due to the fact that it goes where other shows would not dare. forget pretty pictures painted for mainstream audiences, forget charm, forget romance...oz does not mess around. the first episode i ever saw struck me as so nasty it was surreal, i  unable say i was ready for it, but as i watched more, i developed a taste for oz, and got accustomed to the high levels of graphic violence. not just violence, but injustice (crooked guards who'll be sold out for a nickel, inmates who'll kill on order and get away with it, well mannered, middle class inmates being turned into prison bitches due to their lack of street skills or prison experience) watching oz, you may become comfortable with what is uncomfortable viewing....that is if you can get in touch with your darker side.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
1   a wonderful little production. <br /><br />the filming technique is very unassuming- very old-time-bbc fashion and gives a comforting, and sometimes discomforting, sense of realism to the entire piece. <br /><br />the actors are extremely well chosen- michael sheen not only "has got all the polari" but he has all the voices down pat too! you can truly see the seamless editing guided by the references to williams' diary entries, not only is it well worth the watching but it is a terrificly written and performed piece. a masterful production about one of the great master's of comedy and his life. <br /><br />the realism really comes home with the little things: the fantasy of the guard which, rather than use the traditional 'dream' techniques remains solid then disappears. it plays on our knowledge and our senses, particularly with the scenes concerning orton and halliwell and the sets (particularly of their flat with halliwell's murals decorating every surface) are terribly well done.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [12]:
# Remove Punctuations
cleaned=[]
i=0
for words in data['review']:
    for punctuation in string.punctuation:
        words = words.replace(punctuation,"")
    for number in '1234567890':
        words = words.replace(number,"")
    data['review'][i] = words
    i = i+1
print ('Data train punctuation removing...')
data.head(20)

Data train punctuation removing...


review  \
0   one of the other reviewers has mentioned that after watching just  oz episode you will be hooked they are right as this is exactly what happened with mebr br the first thing that struck me about oz was it is brutality and unflinching scenes of violence which set in right from the word go trust me this is not a show for the faint hearted or timid this show pulls no punches with regards to drugs sex or violence it is is hardcore in the classic use of the wordbr br it is called oz as that is the nickname given to the oswald maximum security state penitentary it focuses mainly on emerald city an experimental section of the prison where all the cells have glass fronts and face inwards so privacy is not high on the agenda em city is home to manyaryans muslims gangstas latinos christians italians irish and moreso scuffles death stares dodgy dealings and shady agreements are never far awaybr br i would say the main appeal of the show is due to the fact that it goes where other shows would not dare forget pretty pictures painted for mainstream audiences forget charm forget romanceoz does not mess around the first episode i ever saw struck me as so nasty it was surreal i  unable say i was ready for it but as i watched more i developed a taste for oz and got accustomed to the high levels of graphic violence not just violence but injustice crooked guards wholl be sold out for a nickel inmates wholl kill on order and get away with it well mannered middle class inmates being turned into prison bitches due to their lack of street skills or prison experience watching oz you may become comfortable with what is uncomfortable viewingthat is if you can get in touch with your darker side                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1   a wonderful little production br br the filming technique is very unassuming very oldtimebbc fashion and gives a comforting and sometimes discomforting sense of realism to the entire piece br br the actors are extremely well chosen michael sheen not only has got all the polari but he has all the voices down pat too you can truly see the seamless editing guided by the references to williams diary entries not only is it well worth the watching but it is a terrificly written and performed piece a masterful production about one of the great masters of comedy and his life br br the realism really comes home with the little things the fantasy of the guard which rather than use the traditional dream techniques remains solid then disappears it plays on our knowledge and our senses particularly with the scenes concerning orton and halliwell and the sets particularly of their flat with halliwells murals decorating every surface are terribly well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

### 3. Stopwords Removing
Remove stopwords from text

In [13]:
cachedStopWords = set(stopwords.words("english"))
for i in range (len(data)):
    meaningful = data['review'].iloc[i]
    meaningful = " ".join([word for word in meaningful.split() if word not in cachedStopWords])
    data['review'].iloc[i]=meaningful
print ('Data trainstop words removing...')
data.head(20)

Data trainstop words removing...


review  \
0   one reviewers mentioned watching oz episode hooked right exactly happened mebr br first thing struck oz brutality unflinching scenes violence set right word go trust show faint hearted timid show pulls punches regards drugs sex violence hardcore classic use wordbr br called oz nickname given oswald maximum security state penitentary focuses mainly emerald city experimental section prison cells glass fronts face inwards privacy high agenda em city home manyaryans muslims gangstas latinos christians italians irish moreso scuffles death stares dodgy dealings shady agreements never far awaybr br would say main appeal show due fact goes shows would dare forget pretty pictures painted mainstream audiences forget charm forget romanceoz mess around first episode ever saw struck nasty surreal unable say ready watched developed taste oz got accustomed high levels graphic violence violence injustice crooked guards wholl sold nickel inmates wholl kill order get away well mannered middle class inmates turned prison bitches due lack street skills prison experience watching oz may become comfortable uncomfortable viewingthat get touch darker side                                                                                                                                                                                                                                                                                                      
1   wonderful little production br br filming technique unassuming oldtimebbc fashion gives comforting sometimes discomforting sense realism entire piece br br actors extremely well chosen michael sheen got polari voices pat truly see seamless editing guided references williams diary entries well worth watching terrificly written performed piece masterful production one great masters comedy life br br realism really comes home little things fantasy guard rather use traditional dream techniques remains solid disappears plays knowledge senses particularly scenes concerning orton halliwell sets particularly flat halliwells murals decorating every surface terribly well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
2   thought wonderful way spend time hot summer weekend sitting air conditioned theater watching lighthearted comedy plot simplistic dialogue witty characters likable even well bread suspected serial killer may disappointed realize unmatch point risk addiction thought proof woody allen still fully control style many us grown lovebr br laughed one woodys comedies years dare say decade never impressed scarlet johanson managed tone sexy image jumped right average spirited young womanbr br may crown jewel career wittier devil wears prada interesting superman great comedy go see friends                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

### 4. Tokenizing
Change words into tokens

In [14]:
stop_words=set(stopwords.words('english'))
tokens = []
for words in data['review']:
    word_tokens = word_tokenize(words)
    words=[]
    for word in ( w for w in word_tokens if not w in stop_words):
        words.append(word)
    tokens.append(words)
print ('Showing results of data train tokenization...\n')
tokens

Showing results of data train tokenization...



[['one',
  'reviewers',
  'mentioned',
  'watching',
  'oz',
  'episode',
  'hooked',
  'right',
  'exactly',
  'happened',
  'mebr',
  'br',
  'first',
  'thing',
  'struck',
  'oz',
  'brutality',
  'unflinching',
  'scenes',
  'violence',
  'set',
  'right',
  'word',
  'go',
  'trust',
  'show',
  'faint',
  'hearted',
  'timid',
  'show',
  'pulls',
  'punches',
  'regards',
  'drugs',
  'sex',
  'violence',
  'hardcore',
  'classic',
  'use',
  'wordbr',
  'br',
  'called',
  'oz',
  'nickname',
  'given',
  'oswald',
  'maximum',
  'security',
  'state',
  'penitentary',
  'focuses',
  'mainly',
  'emerald',
  'city',
  'experimental',
  'section',
  'prison',
  'cells',
  'glass',
  'fronts',
  'face',
  'inwards',
  'privacy',
  'high',
  'agenda',
  'em',
  'city',
  'home',
  'manyaryans',
  'muslims',
  'gangstas',
  'latinos',
  'christians',
  'italians',
  'irish',
  'moreso',
  'scuffles',
  'death',
  'stares',
  'dodgy',
  'dealings',
  'shady',
  'agreements',
  'nev

### 5. Stemming
Change words into stemmed words in the Porter Stemmer list

In [15]:
#stemming data
cleandata = []
for words in tokens:
    word=[]
    for i in range (0, len(words)):
        ps = PorterStemmer()
        review = [ps.stem(words[i])]
        review = ' '.join(review)
        word.append(review)
    cleandata.append(word)
print ('Showing result of data train stemming...')
cleandata

i=0
for words in cleandata:
    sentences=' '.join(words)
    data['review'][i]=sentences
    i=i+1
print ('Showing cleaned data train...')
data.head(20)

Showing result of data train stemming...
Showing cleaned data train...


review  \
0   one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side                                                                                                                                                                                                                                                                 
1   wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
2   thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
3   basic famili littl boy jake think zombi closet parent fight timebr br movi slowe

### Split the dataset

#train dataset
train_reviews = data.review[:30000]
train_sentiment = data.sentiment[:30000]
#test dataset
test_reviews = data.review[30000:]
test_sentiment = data.sentiment[30000:]

#Shape of train & test dataset
print('Shape of train dataset::',train_reviews.shape,train_sentiment.shape)
print('Shape of test dataset::',test_reviews.shape,test_sentiment.shape)
train_reviews

# Feature Extraction
### 1. Bag of Words CountVectorizer

In [16]:
cv = CountVectorizer(ngram_range=(1,1))
dataCount = cv.fit_transform(data['review'])
#test_cv = cv.transform(norm_test_reviews)
#review_countVect = cv.fit_transform(data['review'])

#print('Shape of data review:', review_countVect.shape)
print('Shape of train_cv::',dataCount.shape)

Shape of train_cv:: (50000, 137790)


In [17]:
print("Number of features : %d \n" %len(cv.get_feature_names()))
print("Show some feature names : \n", cv.get_feature_names()[::100])

Number of features : 137790 

Show some feature names : 
 ['aa', 'abank', 'abishag', 'aboutsay', 'abstrus', 'accentsget', 'accouter', 'aciton', 'actingaw', 'actionbas', 'actionther', 'actorskristin', 'actto', 'addictingmostli', 'adjustbr', 'adrenalinepump', 'adversarybr', 'affaira', 'aforeprais', 'afterther', 'againugh', 'aggamemnon', 'agraw', 'ahhth', 'air', 'aitd', 'akyroid', 'albizu', 'alexanad', 'alienonearth', 'allanc', 'alliancesi', 'allstar', 'almast', 'alongid', 'alsoif', 'altruism', 'amann', 'ambigu', 'americancowboywestern', 'amitabhhema', 'amrohi', 'anarchist', 'andcom', 'andov', 'andther', 'angelmort', 'anihili', 'anjalith', 'announcedbr', 'answer', 'antibibl', 'antifemin', 'antipakistan', 'antiwoman', 'anykind', 'anywherewow', 'aphorist', 'apparentlyonli', 'appoach', 'aquarian', 'archbishop', 'areanow', 'aregener', 'areshap', 'argu', 'armaan', 'arndt', 'arrivist', 'arthuriophil', 'artthough', 'ashcroftbr', 'askeygand', 'assbut', 'asterix', 'atav', 'atmospherebr', 'attemtp'

In [18]:
print ('Showing the vector of vocabularies...')
cv.vocabulary_

Showing the vector of vocabularies...


{'girlfriendinacoma': 48094,
 'saulbr': 104152,
 'brigitta': 15484,
 'lopera': 70221,
 'swungbr': 118302,
 'propelledbr': 95552,
 'expedi': 39439,
 'disappointmentsmost': 32006,
 'thelma': 120762,
 'hitandmissst': 55222,
 'duke': 34755,
 'hutchenc': 57536,
 'retrouvé': 100369,
 'estoril': 38271,
 'festivalh': 41810,
 'minah': 76506,
 'sytl': 118508,
 'hack': 51410,
 'marinenav': 73122,
 'bittorr': 12585,
 'nye': 84662,
 'badnow': 8983,
 'antibuddi': 5108,
 'topgun': 123358,
 'nineyear': 82665,
 'fez': 41885,
 'sadli': 103189,
 'monstruou': 78092,
 'natail': 81149,
 'daumier': 28793,
 'pedecariss': 89969,
 'crucibl': 27257,
 'althoughlik': 3564,
 'psmith': 96013,
 'actuallybut': 1209,
 'domebr': 33119,
 'veronica': 129529,
 'endingwhat': 37133,
 'slowtediouslyin': 111048,
 'buttstomp': 17114,
 'physiolog': 91373,
 'flyin': 43741,
 'stingri': 115136,
 'longdeceas': 69956,
 'shoplift': 108805,
 'mamer': 72405,
 'redbr': 98941,
 'postaft': 93665,
 'lifesav': 68687,
 'brows': 15939,
 'despl

In [19]:
print ('Creating data train Bag of Words...\n')
print ("{} sentences and {} unique words create a matrix of the shape {}.".format(
      len(data['review']),
      len(cv.get_feature_names()),
      dataCount.toarray().shape,
))
#Create the bag of words matrix
dataCount_BoW = dataCount.toarray()
dataCount_BoW

Creating data train Bag of Words...

50000 sentences and 137790 unique words create a matrix of the shape (50000, 137790).


array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ..., 
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

## Split Data Into Training Set and Validation Set

In [20]:
print ('Split data into 80% training set and 20% validation set...')
X_train, X_val, y_train, y_val = train_test_split(data['review'], data['sentiment'], test_size=0.2, random_state=2)
print ('\nLoad %d training set...\n' %(X_train.shape[0]))
print ('Show a review in the training set:\n', X_train.iloc[1])

print ('\nLoad %d validation set...\n' %(X_val.shape[0]))
print ('Show a review in the validation set:\n', X_val.iloc[1])

Split data into 80% training set and 20% validation set...

Load 40000 training set...

Show a review in the training set:
 oh boy oh boy movi someth lover real cineatiqu art realli uncap sens total bore especi anticlimax peopl behav strang unrealist sometim feel like sit theatr dialogu actor tend face camera therefor audienc instead like said art movi shown cann go better leav movi alon disappoint end know wast time like two thumb

Load 10000 validation set...

Show a review in the validation set:
 first seri brilliant easili one best horror film time crappiest sat watch actual think bad fourth fifth one would good previou terribl one boy wrong incred wrongbr br watch first ten minut actual realli tempt turn thought mayb itll improv notbr br dire film need anoth sequel last two fourth fifth alreadi terribl enough also mani time bring freddi back act terribl storylin predict crap also flaw well way made springwood total wrong pay respect first one atal add whole thing seem realli overt

In [21]:
print ('Showing the list of data labels...')
sentiment_list = list(y_train.value_counts().index)
sentiment_list

Showing the list of data labels...


['negative', 'positive']

In [22]:
X_train_countVect=cv.fit_transform(X_train)
print ("Number of data train, number of terms : ", X_train_countVect.shape)

Number of data train, number of terms :  (40000, 120789)


In [23]:
X_val_countVect=cv.transform(X_val)
print ("Number of validation set, number of terms:", X_val_countVect.shape)

Number of validation set, number of terms: (10000, 120789)


In [24]:
neg=len([x for x in y_train if x == 'negative'])
pos=len([x for x in y_train if x == 'positive'])
neg, pos

(20021, 19979)

In [25]:
neg=len([x for x in y_val if x == 'negative'])
pos=len([x for x in y_val if x == 'positive'])
neg, pos

(4979, 5021)

## TF IDF
Fit and transform the training data to a document-term matrix using TfidfVectorizer

#Tfidf vectorizer
tv = TfidfVectorizer(min_df=0,max_df=1,use_idf=True,ngram_range=(1,3))
#transformed train reviews
tv_train_reviews = tv.fit_transform(train_reviews)
#transformed test reviews
tv_test_reviews = tv.transform(test_reviews)
print('Tfidf_train:',tv_train_reviews.shape)
print('Tfidf_test:',tv_test_reviews.shape)

In [26]:
print ('Fit and transform the training data to a document-term matrix using TfidfVectorizer...')
tfidf = TfidfVectorizer(min_df=2) #minimum document frequency of 2\
X_train_tfidf = tfidf.fit_transform(X_train)

Fit and transform the training data to a document-term matrix using TfidfVectorizer...


In [27]:
print ('Fit and transform the training data to a document-term matrix using TfidfTransformer...')
tfidf_transformer = TfidfTransformer()
X_train_tfidf = tfidf_transformer.fit_transform(X_train_countVect)
X_train_tfidf.shape

Fit and transform the training data to a document-term matrix using TfidfTransformer...


(40000, 120789)

In [28]:
print ("{} sentences and {} unique words create a matrix of the train shape {}.".format(
    len(data),
    len(tfidf.get_feature_names()),
    X_train_tfidf.toarray().shape
))
X_train_tfidf.toarray()

50000 sentences and 48019 unique words create a matrix of the train shape (40000, 120789).


array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       ..., 
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.]])

In [29]:
X_val_tfidf = tfidf_transformer.transform(X_val_countVect)
X_val_tfidf.shape

(10000, 120789)

In [30]:
print ("{} sentences and {} unique words create a matrix of the validation shape {}.".format(
    len(data),
    len(tfidf.get_feature_names()),
    X_val_tfidf.toarray().shape
))
X_val_tfidf.toarray()

50000 sentences and 48019 unique words create a matrix of the validation shape (10000, 120789).


array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       ..., 
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.]])

In [31]:
# Print model evaluation to predicted result
def modelEvaluation(predictions):
    print ("\nAccuracy on validation set: {:.4f}".format(accuracy_score(y_val, predictions)))
    print ("\nClassification report : \n", metrics.classification_report(y_val, predictions))
    print ("\nConfusion Matrix : \n", metrics.confusion_matrix(y_val, predictions))
    

## Training Model 
### Support Vector Machine

#training the linear svm
svm = SGDClassifier(loss='hinge', random_state=42)
#fitting the svm for bag of words
svm_bow = svm.fit(train_cv, train_sentiments)
print(svm_bow)
#fitting the svm for tfidf features
svm_tfidf = svm.fit(tv_train_reviews, train_sentiments)
print(svm_tfidf)

In [32]:
print ("Training the Support Vector Machine...\n")

svc = SVC(kernel='linear',C=1).fit(X_train_tfidf, y_train)
svc_predictions = svc.predict(X_val_tfidf)
print (svc)

Training the Support Vector Machine...

SVC(C=1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)


### Model Classification

In [33]:
print ("Support Vector Machine prediction results...\n")
print (svc_predictions)

Support Vector Machine prediction results...

['negative' 'negative' 'positive' ..., 'negative' 'positive' 'positive']


In [34]:
print ("SVM evaluation results...\n")
modelEvaluation(svc_predictions)

SVM evaluation results...


Accuracy on validation set: 0.8951

Classification report : 
              precision    recall  f1-score   support

   negative       0.90      0.89      0.89      4979
   positive       0.89      0.90      0.90      5021

avg / total       0.90      0.90      0.90     10000


Confusion Matrix : 
 [[4424  555]
 [ 494 4527]]


# Classification Data Test

In [35]:
test_data = pd.read_csv('./Downloads/test.csv')

In [36]:
test_data.head()

text
0  Just finished watching this pre-Code movie called Night Nurse starring Barbara Stanwyck on VHS as one in several of a series of videocassettes named "Forbidden Hollywood" hosted by Leonard Maltin. Before the picture starts Maltin tells of and shows many scenes that a few years after the year this film was made (1931) wouldn't have been allowed. Like scenes of Ms. Stanwyck and Joan Blondell undressing or of a bootlegger (Ben Lyon) getting away with murder. Clark Gable, in one of his early roles, impresses greatly in his scenes with Barbara as the brutal chauffeur who's in cahoots with the crooked doctor in her hospital. And it's always a treat to see Charles Winninger in another one of his kindly elderly paternal roles, here as Stanwyck's moral superior. And seeing Blondell and Lyon with the leading lady are such a treat that I'm now curious if they did anything else together. Quickly and efficiently helmed by William Wellman who directed James Cagney to stardom in The Public Enemy the same year, Night Nurse is one of his more underrated gems.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
1  As a big fan of indie and low budget horror, I've seen some poor acting in my day, but this one may take the cake. I think the cast knew what they had gotten themselves into and stopped trying after the read through.Basically, this film commits the cardinal triple sin of the indie horror world: The script is stupid, its boring, and its not at all scary.I'm one of those people who feels he is required to sit all the way through any movie, but this one tempted me to bail out like no other movie I've seen recently. I did make it though, barely.As for the people who are comparing this to Blair Witch, why? The two films have nothing in common at all, other than having a scene or two take place in the woods.Save your rental money....or go rent Session 9, May, or Ginger Snaps instead.Rating 1 of 10.                                                                                                                                                    

In [39]:
test_data['sentiment'] = test_data.apply(lambda row: '')

In [41]:
test_data.head()

text  \
0  Just finished watching this pre-Code movie called Night Nurse starring Barbara Stanwyck on VHS as one in several of a series of videocassettes named "Forbidden Hollywood" hosted by Leonard Maltin. Before the picture starts Maltin tells of and shows many scenes that a few years after the year this film was made (1931) wouldn't have been allowed. Like scenes of Ms. Stanwyck and Joan Blondell undressing or of a bootlegger (Ben Lyon) getting away with murder. Clark Gable, in one of his early roles, impresses greatly in his scenes with Barbara as the brutal chauffeur who's in cahoots with the crooked doctor in her hospital. And it's always a treat to see Charles Winninger in another one of his kindly elderly paternal roles, here as Stanwyck's moral superior. And seeing Blondell and Lyon with the leading lady are such a treat that I'm now curious if they did anything else together. Quickly and efficiently helmed by William Wellman who directed James Cagney to stardom in The Public Enemy the same year, Night Nurse is one of his more underrated gems.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
1  As a big fan of indie and low budget horror, I've seen some poor acting in my day, but this one may take the cake. I think the cast knew what they had gotten themselves into and stopped trying after the read through.Basically, this film commits the cardinal triple sin of the indie horror world: The script is stupid, its boring, and its not at all scary.I'm one of those people who feels he is required to sit all the way through any movie, but this one tempted me to bail out like no other movie I've seen recently. I did make it though, barely.As for the people who are comparing this to Blair Witch, why? The two films have nothing in common at all, other than having a scene or two take place in the woods.Save your rental money....or go rent Session 9, May, or Ginger Snaps instead.Rating 1 of 10.                                                                                                                                              

## Data-test preprocessing
### 1 Case Folding

In [42]:
pd.set_option('display.max_colwidth',-1)
for i in range(len(data)):
    lowercase = str.lower(test_data['text'].iloc[i])
    test_data['text'].iloc[i]=lowercase
#print 'Data train case folding...'
test_data.head()

text  \
0  just finished watching this pre-code movie called night nurse starring barbara stanwyck on vhs as one in several of a series of videocassettes named "forbidden hollywood" hosted by leonard maltin. before the picture starts maltin tells of and shows many scenes that a few years after the year this film was made (1931) wouldn't have been allowed. like scenes of ms. stanwyck and joan blondell undressing or of a bootlegger (ben lyon) getting away with murder. clark gable, in one of his early roles, impresses greatly in his scenes with barbara as the brutal chauffeur who's in cahoots with the crooked doctor in her hospital. and it's always a treat to see charles winninger in another one of his kindly elderly paternal roles, here as stanwyck's moral superior. and seeing blondell and lyon with the leading lady are such a treat that i'm now curious if they did anything else together. quickly and efficiently helmed by william wellman who directed james cagney to stardom in the public enemy the same year, night nurse is one of his more underrated gems.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
1  as a big fan of indie and low budget horror, i've seen some poor acting in my day, but this one may take the cake. i think the cast knew what they had gotten themselves into and stopped trying after the read through.basically, this film commits the cardinal triple sin of the indie horror world: the script is stupid, its boring, and its not at all scary.i'm one of those people who feels he is required to sit all the way through any movie, but this one tempted me to bail out like no other movie i've seen recently. i did make it though, barely.as for the people who are comparing this to blair witch, why? the two films have nothing in common at all, other than having a scene or two take place in the woods.save your rental money....or go rent session 9, may, or ginger snaps instead.rating 1 of 10.                                                                                                                                              

### 2 Normalization
Convert words into normalized words, convert negation, and remove punctuations.

In [43]:
# Convert words into normalized words
normalization = csv.reader(open('./Downloads/Corpus/normalisasi.csv', 'r'))

d = {}
for row in normalization:
    k,v= row
    d[str.lower(k)] = str.lower(v)
pat = re.compile(r"\b(%s)\b" % "|".join(d))

for i in range(len(data)):
    text = str.lower(test_data['text'].iloc[i])
    normal = pat.sub(lambda m: d.get(m.group()), text)
    test_data['text'].iloc[i]=normal 
print ('Data train normalization...')
data.head()

Data train normalization...


review  \
0  one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side   
1  wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2  thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  basic famili littl boy jake think zombi closet parent fight timebr br movi slower soap opera suddenli jake decid becom rambo kill zombiebr br good first youar go make film must decid thriller drama drama movi watchabl parent divorc argu like real life jake closet total ruin film expect see boogeyman similar movi instead watch drama meaningless thriller spotsbr br well play parent descent dialog shot jake ignor                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [44]:
# Convert Negation
negation = csv.reader(open('./Downloads/Corpus/convert negation.csv', 'r'))

d = {}
for row in negation:
    k,v= row
    d[str.lower(k)] = str.lower(v)
    #print d[k]
pat = re.compile(r"\b(%s)\b" % "|".join(d))
for i in range(len(data)):
    convert = str.lower(test_data['text'].iloc[i])
    convert = pat.sub(lambda m: d.get(m.group()), convert)
    test_data['text'].iloc[i]=convert
print ('Data train negation word converting...')
data.head()

Data train negation word converting...


review  \
0  one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side   
1  wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2  thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  basic famili littl boy jake think zombi closet parent fight timebr br movi slower soap opera suddenli jake decid becom rambo kill zombiebr br good first youar go make film must decid thriller drama drama movi watchabl parent divorc argu like real life jake closet total ruin film expect see boogeyman similar movi instead watch drama meaningless thriller spotsbr br well play parent descent dialog shot jake ignor                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [45]:
# Remove Punctuations
cleaned=[]
i=0
for words in test_data['text']:
    for punctuation in string.punctuation:
        words = words.replace(punctuation,"")
    for number in '1234567890':
        words = words.replace(number,"")
    test_data['text'][i] = words
    i = i+1
print ('Data train punctuation removing...')
data.head()

Data train punctuation removing...


review  \
0  one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side   
1  wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2  thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  basic famili littl boy jake think zombi closet parent fight timebr br movi slower soap opera suddenli jake decid becom rambo kill zombiebr br good first youar go make film must decid thriller drama drama movi watchabl parent divorc argu like real life jake closet total ruin film expect see boogeyman similar movi instead watch drama meaningless thriller spotsbr br well play parent descent dialog shot jake ignor                                                                                                                                                                                                                                                                                                                                                                                                                                                 

### 3. Stopwords Removing
Remove stopwords from text

In [46]:
cachedStopWords = set(stopwords.words("english"))
for i in range (len(data)):
    meaningful = test_data['text'].iloc[i]
    meaningful = " ".join([word for word in meaningful.split() if word not in cachedStopWords])
    test_data['text'].iloc[i]=meaningful
print ('Data trainstop words removing...')
data.head()

Data trainstop words removing...


review  \
0  one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side   
1  wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2  thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  basic famili littl boy jake think zombi closet parent fight timebr br movi slower soap opera suddenli jake decid becom rambo kill zombiebr br good first youar go make film must decid thriller drama drama movi watchabl parent divorc argu like real life jake closet total ruin film expect see boogeyman similar movi instead watch drama meaningless thriller spotsbr br well play parent descent dialog shot jake ignor                                                                                                                                                                                                                                                                                                                                                                                                                                                 

### 4. Tokenizing
Change words into tokens


In [47]:
stop_words=set(stopwords.words('english'))
tokens = []
for words in test_data['text']:
    word_tokens = word_tokenize(words)
    words=[]
    for word in ( w for w in word_tokens if not w in stop_words):
        words.append(word)
    tokens.append(words)
print ('Showing results of data train tokenization...\n')
tokens

Showing results of data train tokenization...



[['finished',
  'watching',
  'precode',
  'movie',
  'called',
  'night',
  'nurse',
  'starring',
  'barbara',
  'stanwyck',
  'vhs',
  'one',
  'several',
  'series',
  'videocassettes',
  'named',
  'forbidden',
  'hollywood',
  'hosted',
  'leonard',
  'maltin',
  'picture',
  'starts',
  'maltin',
  'tells',
  'shows',
  'many',
  'scenes',
  'years',
  'year',
  'film',
  'made',
  'would',
  'lost',
  'allowed',
  'like',
  'scenes',
  'ms',
  'stanwyck',
  'joan',
  'blondell',
  'undressing',
  'bootlegger',
  'ben',
  'lyon',
  'getting',
  'away',
  'murder',
  'clark',
  'gable',
  'one',
  'early',
  'roles',
  'impresses',
  'greatly',
  'scenes',
  'barbara',
  'brutal',
  'chauffeur',
  'whos',
  'cahoots',
  'crooked',
  'doctor',
  'hospital',
  'always',
  'treat',
  'see',
  'charles',
  'winninger',
  'another',
  'one',
  'kindly',
  'elderly',
  'paternal',
  'roles',
  'stanwycks',
  'moral',
  'superior',
  'seeing',
  'blondell',
  'lyon',
  'leading',
  'lad

### 5. Stemming
Change words into stemmed words in the Porter Stemmer list

In [48]:
#stemming data
cleandata = []
for words in tokens:
    word=[]
    for i in range (0, len(words)):
        ps = PorterStemmer()
        text = [ps.stem(words[i])]
        text = ' '.join(text)
        word.append(text)
    cleandata.append(word)
print ('Showing result of data train stemming...')
cleandata

i=0
for words in cleandata:
    sentences=' '.join(words)
    test_data['text'][i]=sentences
    i=i+1
print ('Showing cleaned data train...')
data.head()

Showing result of data train stemming...
Showing cleaned data train...


review  \
0  one review mention watch oz episod hook right exactli happen mebr br first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use wordbr br call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home manyaryan muslim gangsta latino christian italian irish moreso scuffl death stare dodgi deal shadi agreement never far awaybr br would say main appeal show due fact goe show would dare forget pretti pictur paint mainstream audienc forget charm forget romanceoz mess around first episod ever saw struck nasti surreal unabl say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard wholl sold nickel inmat wholl kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort viewingthat get touch darker side   
1  wonder littl product br br film techniqu unassum oldtimebbc fashion give comfort sometim discomfort sens realism entir piec br br actor extrem well chosen michael sheen got polari voic pat truli see seamless edit guid refer william diari entri well worth watch terrificli written perform piec master product one great master comedi life br br realism realli come home littl thing fantasi guard rather use tradit dream techniqu remain solid disappear play knowledg sens particularli scene concern orton halliwel set particularli flat halliwel mural decor everi surfac terribl well done                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2  thought wonder way spend time hot summer weekend sit air condit theater watch lightheart comedi plot simplist dialogu witti charact likabl even well bread suspect serial killer may disappoint realiz unmatch point risk addict thought proof woodi allen still fulli control style mani us grown lovebr br laugh one woodi comedi year dare say decad never impress scarlet johanson manag tone sexi imag jump right averag spirit young womanbr br may crown jewel career wittier devil wear prada interest superman great comedi go see friend                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  basic famili littl boy jake think zombi closet parent fight timebr br movi slower soap opera suddenli jake decid becom rambo kill zombiebr br good first youar go make film must decid thriller drama drama movi watchabl parent divorc argu like real life jake closet total ruin film expect see boogeyman similar movi instead watch drama meaningless thriller spotsbr br well play parent descent dialog shot jake ignor                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [49]:
#laplace smoothing
def predict(self, X):
    result = []
    for text in X:
      class_scores = {c: self.log_class_priors[c] for c in self.classes}
      words = set(self.tokenizer.tokenize(text))

      for word in words:
          if word not in self.vocab: continue

          for c in self.classes:

            log_w_given_c = self.laplace_smoothing(word, c)
            class_scores[c] += log_w_given_c

      result.append(max(class_scores, key=class_scores.get))

    return result

In [50]:
def laplace_smoothing(self, word, text_class):
  num = self.word_counts[text_class][word] + 1
  denom = self.n_class_items[text_class] + len(self.vocab)
  return math.log(num / denom)

In [51]:
i=0
for words in cleandata:
    sentences=' '.join(words)
    test_data['text'][i]=sentences
    i=i+1
print ('Showing result of Preprocessed xiaomi data...')
test_data.head()

Showing result of Preprocessed xiaomi data...


text  \
0  finish watch precod movi call night nurs star barbara stanwyck vh one sever seri videocassett name forbidden hollywood host leonard maltin pictur start maltin tell show mani scene year year film made would lost allow like scene ms stanwyck joan blondel undress bootlegg ben lyon get away murder clark gabl one earli role impress greatli scene barbara brutal chauffeur who cahoot crook doctor hospit alway treat see charl winning anoth one kindli elderli patern role stanwyck moral superior see blondel lyon lead ladi treat curiou anyth els togeth quickli effici helm william wellman direct jame cagney stardom public enemi year night nurs one underr gem                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
1  big fan indi low budget horror seen poor act day one may take cake think cast knew gotten stop tri read throughbas film commit cardin tripl sin indi horror world script stupid bore scaryi one peopl feel requir sit way movi one tempt bail like movi seen recent make though barelya peopl compar blair witch two film noth common scene two take place woodssav rental moneyor go rent session may ginger snap insteadr                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
2  winter compel stori base novel written evan maxwel divid two part contain strong messag first part agent dane corvin richard chamberlain pose businessman interest buy fish illeg caught member swinomish indian tribal commun law pass limit fish protect fish resourc area make imposs commun continu live tradit salmon shellfish fish

In [52]:
X_train_new=test_data['text']
y_train_new=test_data['sentiment']
print ('Loading %d training set...\n'%(X_train_new.shape[0]))
print ('Showing some training set examples...')
X_train_new.head()

Loading 50000 training set...

Showing some training set examples...


0    finish watch precod movi call night nurs star barbara stanwyck vh one sever seri videocassett name forbidden hollywood host leonard maltin pictur start maltin tell show mani scene year year film made would lost allow like scene ms stanwyck joan blondel undress bootlegg ben lyon get away murder clark gabl one earli role impress greatli scene barbara brutal chauffeur who cahoot crook doctor hospit alway treat see charl winning anoth one kindli elderli patern role stanwyck moral superior see blondel lyon lead ladi treat curiou anyth els togeth quickli effici helm william wellman direct jame cagney stardom public enemi year night nurs one underr gem                                                                                                                                                                                                                                                                                                                                                      

In [ ]:
X_movie = test_data['yext']
y_movie = test_data['Sentiment']
print ('Loading %d Samsung dataset...\n'%(X_samsung.shape[0]))
print ('Showing some training set examples...')
X_movie.head()

## Feature Extraction
### TF-IDF Vectorizer

In [53]:
tfidf = TfidfVectorizer(min_df=2) #minimum document frequency of 2
X_train_new_tfidf = tfidf.fit_transform(X_train_new)

print("Number of features : %d \n" %len(tfidf.get_feature_names()))
print("Show some feature names : \n", tfidf.get_feature_names()[::1])

Number of features : 56278 

Show some feature names : 
 ['aa', 'aaa', 'aaaaargh', 'aaaah', 'aaah', 'aaahhh', 'aaargh', 'aah', 'aaja', 'aaliyah', 'aam', 'aamir', 'aandhi', 'aap', 'aapk', 'aapko', 'aardman', 'aargh', 'aaron', 'aarti', 'aav', 'aaya', 'ab', 'aback', 'abandon', 'abas', 'abash', 'abat', 'abattoir', 'abba', 'abbasmustan', 'abberlin', 'abberton', 'abbey', 'abbi', 'abbot', 'abbott', 'abbottcostello', 'abbrevi', 'abc', 'abcd', 'abctv', 'abd', 'abdic', 'abdomen', 'abdomin', 'abduct', 'abducte', 'abductor', 'abdul', 'abduljabbar', 'abdullah', 'abdulov', 'abe', 'abel', 'abercrombi', 'aberjhani', 'aberr', 'aberystwyth', 'abet', 'abhishek', 'abhor', 'abhorr', 'abi', 'abid', 'abigail', 'abil', 'abilitiesa', 'abilitiesit', 'abilitiessom', 'abilityi', 'abilityther', 'abit', 'abject', 'abjectli', 'abl', 'ablaz', 'ablebodi', 'abli', 'ablut', 'abner', 'abnorm', 'aboard', 'abod', 'abolish', 'abolit', 'abolitionist', 'abomb', 'abomin', 'aboot', 'aborigin', 'abort', 'abortionist', 'abott', '

In [54]:
countVect = CountVectorizer(ngram_range=(1,1))
X_train_new_countVect = countVect.fit_transform(X_train_new) 
X_train_new_countVect.shape

(50000, 177505)

In [ ]:
tfidf_new_transformer = TfidfTransformer()
X_train_new_tfidf = tfidf_new_transformer.fit_transform(X_train_new_countVect)
X_train_new_tfidf.shape

In [ ]:
movie_countVect = countVect.transform(X_movie)
movie_tfidf = tfidf_transformer.fit_transform(movie_countVect)
movie_tfidf.shape

## Training Data Train
### Support Vector Machine

In [ ]:
svc = SVC(kernel='linear', C=1).fit(X_train_new_tfidf, y_train_new)
svc_movie_predictions = svc.predict(X_samsung_tfidf)

### Result

In [ ]:
movie_test_predictions

In [ ]:
csvfile = "Desktop/svc_samsung_predictions.csv"
with open(csvfile, "w") as output:
    writer = csv.writer(output, lineterminator='\n')
    writer.writerows(movie_test_predictions)

In [ ]:
movie_neg_svc = len([x for x in movie_test_predictions if x == u'0'])
movie_pos_svc = len([x for x in movie_test_predictions if x == u'1'])
movie_neg_svc,movie_pos_svc

In [ ]:
movie_BR_svc = float(movie_pos_svc - movie_neg_svc)
movie_BR_svc

In [ ]:
movie_NBR_svc= (movie_BR_svc/(movie_pos_svc + movie_neg_svc))*100
movie_NBR_svc

### Visualization

In [ ]:
N=3
ind = np.arange(N)
width=0.25
fig, ax = plt.subplots()

movie = (movie_NBR_svc)
movie_std = (2,3,4)
rects1 = ax.bar(ind, movie, width, color='turquoise', yerr=movie_std)

ax.set_ylabel('Scores')
ax.set_xticklabels(('SVM'))
ax.legend((('movie')), loc=(0, -.38))

def autolabel(rects):
    for rect in rects:
        height = rect.get_height()
        ax.text(rect.get_x()+rect.get_width()/1.25,1.025*height,'%d'%int(height), ha='center',va='bottom')   
autolabel(rects1)
plt.show